In [1]:
import numpy as np
import pandas as pd
from astropy.time import Time
import h5py
from pycbc.conversions import mchirp_from_mass1_mass2,primary_mass,secondary_mass,chi_eff
import pylab,os,shutil
import matplotlib.pyplot as plt
pd.set_option('display.max_columns',None)

# Select those interesting triggers

In [2]:
fourogc = h5py.File('/work/ahnitz/WWW/4ogc/4-ogc.hdf')

In [3]:
i=np.where(fourogc['name'][:]==b'190701_223255')

In [4]:
fourogc['time'][i]

array([1.24605559e+09])

In [5]:
Time(fourogc['time'][i],format='gps').datetime64

array(['2019-07-01T22:33:32.652099609'], dtype='datetime64[ns]')

In [6]:
gwfile = fourogc

# convert the GW events name to UTF-8 format
gwobs = np.array([obs.decode("utf-8") for obs in gwfile['trig'][:]])

mass1 = np.array(gwfile['mass1'])
mass2 = np.array(gwfile['mass2'])
spin1z = np.array(gwfile['spin1z'])
spin2z = np.array(gwfile['spin2z'])
spin = chi_eff(gwfile['mass1'][:], gwfile['mass2'][:],gwfile['spin1z'][:], gwfile['spin2z'][:])
name_gw = np.array(gwfile['name'])
ifar = np.array(gwfile['ifar'])
time_gw = np.array(gwfile['time'])

In [7]:
lmass = (mass2<=2) & (mass1<=2)
lspin = (spin<0.2) & (spin>-0.2)

#at least two detectors
# This doesn't affect the results because single detector trigger doesn't have a IFAR
ltrig = (gwobs == 'HL') | (gwobs == 'HLV') | (gwobs == 'LV') | (gwobs == 'HV')

#false alarm rate < every 10 min
yr2min = 365.25*24*60
lifar = (gwfile['ifar'][:] > 1/yr2min * 1)
lifar = True
#ltrig = True

# time during O3a start and 2019 07, 02 00:00:00
ltime = (gwfile['time'][:] > Time('2019-04-01T00:00:00').gps) & (gwfile['time'][:] < Time('2019-07-02T00:00:00').gps)
l = lmass & lspin & ltrig & lifar & ltime
print('There are ', l.sum(), ' triggers')

# the index of a qualified GW event
gwidx = np.where(l)[0]

There are  294489  triggers


In [8]:
gwobs = gwobs[gwidx]
mass1 = mass1[gwidx]
mass2 = mass2[gwidx]
spin1z = spin1z[gwidx]
spin2z = spin2z[gwidx]
name_gw = name_gw[gwidx]
ifar = ifar[gwidx]
time_gw = time_gw[gwidx]

In [9]:
len(time_gw)

294489

In [10]:
np.where(time_gw[1:]-time_gw[:-1]<=0)

(array([], dtype=int64),)

# FRB

In [11]:
#FRB file: CHIME FRB catalog 1
frb = pd.read_csv('/work/yifan.wang/em/gitrepo/chimefrbcat1.csv')
# convert the mjd_inf time to a datetime64 format
frb_t =  Time(frb['mjd_inf'][:],format='mjd').datetime64

tO3_start = Time('2019-04-01T00:00:00')
tO3_end = Time('2019-07-02T00:00:00')

frb = frb[(frb_t <tO3_end) & (frb_t > tO3_start) & (frb['repeater_name'] == '-9999')] #not a repeated FRB

In [12]:
#add a new column called 'gpstime'
frb['gpstime'] = Time(frb['mjd_inf'][:],format='mjd').gps

#make four arrays which will be useful
t_frb = np.array(frb['gpstime'])
name_frb = np.array(frb['tns_name'])
ra_frb = np.array(frb['ra'])/ 180 * np.pi
dec_frb = np.array(frb['dec']) / 180 * np.pi

# There are 151 FRB events

In [13]:
name_frb, uid = np.unique(name_frb, return_index=True)
ra_frb = ra_frb[uid]
dec_frb = dec_frb[uid]
t_frb = t_frb[uid]

In [14]:
uid

array([  0,   1,   3,   4,   5,   6,   7,   8,   2,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  39,  38,
        40,  41,  43,  42,  46,  48,  50,  51,  52,  53,  54,  55,  56,
        57,  58,  59,  61,  60,  62,  63,  65,  66,  67,  68,  69,  70,
        71,  73,  72,  74,  75,  76,  77,  78,  79,  80,  81,  82,  83,
        84,  85,  87,  88,  89,  90,  91,  92,  93,  94,  95,  97,  96,
        99, 102, 100, 101, 103, 104, 105, 106, 107, 108, 109, 110, 112,
       113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125,
       126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138,
       139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151,
       152, 153, 154, 155, 156, 157, 158, 159])

In [15]:
len(ra_frb)

151

In [16]:
np.where(name_frb=='FRB20190425A')

(array([48]),)

In [17]:
name_frb[48:]

array(['FRB20190425A', 'FRB20190425B', 'FRB20190426A', 'FRB20190427A',
       'FRB20190428A', 'FRB20190429A', 'FRB20190429B', 'FRB20190430A',
       'FRB20190430B', 'FRB20190430C', 'FRB20190501B', 'FRB20190502A',
       'FRB20190502B', 'FRB20190502C', 'FRB20190515A', 'FRB20190515B',
       'FRB20190515D', 'FRB20190516B', 'FRB20190517C', 'FRB20190517D',
       'FRB20190518B', 'FRB20190518C', 'FRB20190518D', 'FRB20190518G',
       'FRB20190519D', 'FRB20190519E', 'FRB20190519F', 'FRB20190519G',
       'FRB20190519H', 'FRB20190519J', 'FRB20190520A', 'FRB20190527A',
       'FRB20190527C', 'FRB20190529A', 'FRB20190530A', 'FRB20190531A',
       'FRB20190531B', 'FRB20190531C', 'FRB20190531E', 'FRB20190601A',
       'FRB20190601B', 'FRB20190601C', 'FRB20190601D', 'FRB20190603B',
       'FRB20190604C', 'FRB20190604D', 'FRB20190604E', 'FRB20190604G',
       'FRB20190605C', 'FRB20190605D', 'FRB20190606B', 'FRB20190607A',
       'FRB20190607B', 'FRB20190608A', 'FRB20190609A', 'FRB20190609B',
      

In [18]:
t_frb[48:]

array([1.24022449e+09, 1.24025074e+09, 1.24027730e+09, 1.24044088e+09,
       1.24046288e+09, 1.24057507e+09, 1.24058722e+09, 1.24065665e+09,
       1.24065120e+09, 1.24066044e+09, 1.24074323e+09, 1.24080621e+09,
       1.24081744e+09, 1.24084778e+09, 1.24196087e+09, 1.24197294e+09,
       1.24198910e+09, 1.24201307e+09, 1.24216601e+09, 1.24214033e+09,
       1.24218717e+09, 1.24220299e+09, 1.24220549e+09, 1.24225445e+09,
       1.24227072e+09, 1.24227173e+09, 1.24227181e+09, 1.24230530e+09,
       1.24231522e+09, 1.24234225e+09, 1.24238311e+09, 1.24300969e+09,
       1.24303099e+09, 1.24319556e+09, 1.24328207e+09, 1.24331487e+09,
       1.24332768e+09, 1.24334480e+09, 1.24335530e+09, 1.24339710e+09,
       1.24344190e+09, 1.24345883e+09, 1.24345772e+09, 1.24357832e+09,
       1.24371467e+09, 1.24365789e+09, 1.24366654e+09, 1.24372516e+09,
       1.24373646e+09, 1.24378876e+09, 1.24389479e+09, 1.24396078e+09,
       1.24396453e+09, 1.24404079e+09, 1.24408357e+09, 1.24413407e+09,
      

In [19]:
t_frb[1:]-t_frb[:-1]

array([ 8.12104504e+04,  7.00596762e+04,  6.14908282e+03,  2.69183250e+04,
        2.03589729e+04,  1.36287167e+04,  3.12577088e+03, -7.70885840e+04,
        1.00702173e+05,  2.82918004e+04,  1.04532452e+05,  2.14043358e+04,
        2.19268491e+05,  4.22240306e+04,  1.17803925e+04,  2.98698669e+04,
        2.01078047e+04,  6.84711867e+04,  4.74284420e+02,  4.37725683e+04,
        1.58078925e+04,  5.15940797e+04,  5.60186782e+04,  1.01579550e+04,
        1.47296412e+05,  1.58672063e+04,  7.03758395e+04,  4.48209017e+04,
        1.56419265e+04,  1.69805761e+04,  6.19806406e+03,  8.71186120e+04,
        5.52198561e+04,  9.07258975e+04,  9.72165457e+03,  7.69311534e+04,
        9.37099822e+03, -2.81301998e+03,  3.67645527e+04,  1.32428454e+05,
        7.83378484e+04, -6.01817639e+04,  9.17618566e+04,  2.83307256e+04,
        1.34622757e+04,  9.24345849e+03,  3.20645436e+04,  1.06995626e+05,
        2.62509015e+04,  2.65559644e+04,  1.63581619e+05,  2.20052814e+04,
        1.12189504e+05,  

In [20]:
sortidx = np.argsort(t_frb)

In [21]:
sortidx

array([  0,   1,   8,   2,   3,   4,   5,   6,   7,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  38,  37,
        39,  40,  42,  41,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  56,  55,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  67,  66,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  90,  89,
        91,  93,  94,  92,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142,
       143, 144, 145, 146, 147, 148, 149, 150])

In [22]:
t_frb = t_frb[sortidx]
ra_frb = ra_frb[sortidx]
dec_frb = dec_frb[sortidx]
name_frb = name_frb[sortidx]

In [23]:
Time(t_frb[np.where(name_frb=='FRB20190701E')],format='gps').datetime64

array(['2019-07-01T22:32:17.497723579'], dtype='datetime64[ns]')

In [24]:
for n in name_frb:
    print(n,Time(t_frb[np.where(name_frb==n)],format='gps').datetime64)

FRB20190401A ['2019-04-01T08:36:43.554188728']
FRB20190402A ['2019-04-02T07:10:14.004630089']
FRB20190403G ['2019-04-03T00:42:45.964979172']
FRB20190403A ['2019-04-03T02:37:53.680835009']
FRB20190403B ['2019-04-03T04:20:22.763651609']
FRB20190403C ['2019-04-03T11:49:01.088608027']
FRB20190403D ['2019-04-03T17:28:20.061472178']
FRB20190403E ['2019-04-03T21:15:28.778144360']
FRB20190403F ['2019-04-03T22:07:34.549023628']
FRB20190404A ['2019-04-04T04:41:08.138349056']
FRB20190404B ['2019-04-04T12:32:39.938773394']
FRB20190405A ['2019-04-05T17:34:52.390566587']
FRB20190405B ['2019-04-05T23:31:36.726361752']
FRB20190408A ['2019-04-08T12:26:05.217539310']
FRB20190409A ['2019-04-09T00:09:49.248150587']
FRB20190409B ['2019-04-09T03:26:09.640700579']
FRB20190409C ['2019-04-09T11:43:59.507593632']
FRB20190409D ['2019-04-09T17:19:07.312287807']
FRB20190410A ['2019-04-10T12:20:18.499004841']
FRB20190410B ['2019-04-10T12:28:12.783424377']
FRB20190411A ['2019-04-11T00:37:45.351679325']
FRB20190411B 

In [25]:
ra_frb[-1],dec_frb[-1]

(2.418502744488542, 1.0770426814057008)

In [26]:
frb[frb['tns_name']=='FRB20190701E']['ra'] / 180 * np.pi

599    2.418503
Name: ra, dtype: float64

In [27]:
frb[frb['tns_name']=='FRB20190701E']['dec'] / 180 * np.pi

599    1.077043
Name: dec, dtype: float64

In [28]:
np.where(t_frb[1:]-t_frb[:-1]<=0)

(array([], dtype=int64),)

In [33]:
import pandas as pd

In [37]:
df = pd.read_csv('candidate.csv')

In [38]:
df

gwname      fix_lnb     relax_lnb    gwstat      ranking
0     190701_223118    11.301643      7.331421  4.952719     8.922941
1     190605_021909    12.771765      9.127000  3.862183     7.506948
2     190411_050213    10.246110      6.976561  3.681050     6.950599
3     190520_102326     5.990904      3.872832  4.148149     6.266221
4     190409_032650    11.120391      7.384171  2.218422     5.954642
...             ...          ...           ...       ...          ...
1045  190519_230244   604.206402    761.931638  2.434241  -155.290995
1046  190612_195828   406.788341    624.079481 -1.029691  -218.320830
1047  190519_230231   840.912410   1060.075528 -3.614769  -222.777887
1048  190518_223900   367.513293    589.391614 -2.869363  -224.747685
1049  190621_081615  8315.252956  12616.639059 -1.468428 -4302.854531

[1050 rows x 5 columns]

# Make triggers: Time window [-100,100]

In [39]:
#[t_frb ---600s--- t_gw ----------- 3600s ------------- t_frb]
left = np.searchsorted(t_frb,  time_gw- 100)
right = np.searchsorted(t_frb, time_gw + 100)

# The index of 'left' is GW index, the value of 'left' is frb index
gw_co_idx = np.where((right - left) > 0)[0]
frb_co_idx = left[gw_co_idx]
print('There are ', len(gw_co_idx), 'coincidence.')

There are  1050 coincidence.


In [40]:
left

array([  1,   1,   1, ..., 151, 151, 151])

In [41]:
len(left)

294489

In [43]:
gw_co_idx

array([  3708,   3709,   3710, ..., 294238, 294239, 294240])

In [45]:
left

array([  1,   1,   1, ..., 151, 151, 151])

In [46]:
len(left)

294489

In [42]:
for n in gw_co_idx:
    print(name_gw[n],Time(time_gw[n],format='gps').datetime64,mass1[n],mass2[n],name_frb[left[n]],ra_frb[left[n]],dec_frb[left[n]])

b'190403_023537' 2019-04-03T02:36:14.228759766 1.1768218056648743 1.032298631645515 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023559' 2019-04-03T02:36:36.370361328 1.434660263451193 1.6251487967038813 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023610' 2019-04-03T02:36:47.379638672 1.6271080385797014 1.7758733682551862 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023639' 2019-04-03T02:37:16.632568359 1.0669656464359942 1.4098445024800907 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023702' 2019-04-03T02:37:39.951904297 1.1069465758723345 1.0521759998174491 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023746' 2019-04-03T02:38:23.626220703 1.3185591071943006 1.3589097399046839 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023816' 2019-04-03T02:38:53.232421875 1.8610107053752478 1.7318110698209905 FRB20190403A 2.0303415188450034 1.507266342022303
b'190403_023841' 2019-04-03T02:39:18.518066406 1.12846535

b'190415_190245' 2019-04-15T19:03:22.473876953 1.1984820831067404 1.5817559240147565 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190415_190300' 2019-04-15T19:03:37.095458984 1.916102833659886 1.043743024507509 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190415_190319' 2019-04-15T19:03:56.745361328 1.0635623932621512 1.950416343148377 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190415_190342' 2019-04-15T19:04:19.187255859 1.0289826150023176 1.2153141687380953 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190415_190401' 2019-04-15T19:04:38.992431641 1.0367869183032654 1.0831862654845377 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190415_190424' 2019-04-15T19:05:01.801757813 1.9923623907691672 1.2588961748003002 FRB20190415B 0.15463617172669758 0.9573130947188897
b'190416_040450' 2019-04-16T04:05:27.317626953 1.0199195122668452 1.5027661292449113 FRB20190416A 2.5305528824665786 0.5811946409141118
b'190416_040509' 2019-04-16T04:05:46.79833984

b'190426_012802' 2019-04-26T01:28:39.146972656 1.844615333106297 1.7025424452997466 FRB20190426A 2.007826771494277 1.0318386537790476
b'190426_012813' 2019-04-26T01:28:50.741210937 1.123161919617519 1.5558101032599212 FRB20190426A 2.007826771494277 1.0318386537790476
b'190426_012834' 2019-04-26T01:29:11.743164063 1.9931927360461148 1.024627263197197 FRB20190426A 2.007826771494277 1.0318386537790476
b'190426_012846' 2019-04-26T01:29:23.044433594 1.0122786406129183 1.0248037100191056 FRB20190426A 2.007826771494277 1.0318386537790476
b'190426_012908' 2019-04-26T01:29:45.527832031 1.1774844473756039 1.1091845168161507 FRB20190426A 2.007826771494277 1.0318386537790476
b'190426_012926' 2019-04-26T01:30:03.486328125 1.9404585848953126 1.0049549503896127 FRB20190426A 2.007826771494277 1.0318386537790476
b'190427_225245' 2019-04-27T22:53:22.849121094 1.0148330426719272 1.0934026138352084 FRB20190427A 1.3775883785991245 0.1356120828799594
b'190427_225300' 2019-04-27T22:53:37.338623047 1.21778480

b'190519_031104' 2019-05-19T03:11:41.341552734 1.9122241392700923 1.023130081471016 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_031119' 2019-05-19T03:11:56.123535156 1.7190310309458223 1.9505070491161842 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_031156' 2019-05-19T03:12:33.078125000 1.0312954615979641 1.6985146624719905 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_031219' 2019-05-19T03:12:56.273681641 1.466038823979464 1.5984229417939722 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_031248' 2019-05-19T03:13:25.872314453 1.0050098268513068 1.0185413853879752 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_031306' 2019-05-19T03:13:43.965087891 1.0423398944913063 1.0552432628291586 FRB20190519D 2.872288350007068 0.7503170454323623
b'190519_032652' 2019-05-19T03:27:29.987060547 1.989747176327268 1.393837226716868 FRB20190519E 2.9370400652560575 0.7269296334556382
b'190519_032724' 2019-05-19T03:28:01.586425781 1.029603146

b'190601_163221' 2019-06-01T16:32:58.292968750 1.0132623045652618 1.7046586804070267 FRB20190601B 0.3120648702565861 0.4157374278250493
b'190601_163240' 2019-06-01T16:33:17.175781250 1.4502339393334727 1.6498239770626513 FRB20190601B 0.3120648702565861 0.4157374278250493
b'190601_205344' 2019-06-01T20:54:21.307128906 1.9456202638218876 1.7150887452876193 FRB20190601D 1.4985396957623311 1.3849187614575003
b'190601_205411' 2019-06-01T20:54:48.777587891 1.5711088474379231 1.431838004158873 FRB20190601D 1.4985396957623311 1.3849187614575003
b'190601_205422' 2019-06-01T20:54:59.166992188 1.0268104438524877 1.8852989990268572 FRB20190601D 1.4985396957623311 1.3849187614575003
b'190601_205432' 2019-06-01T20:55:09.716552734 1.9072149627193236 1.0351723213384485 FRB20190601D 1.4985396957623311 1.3849187614575003
b'190601_205505' 2019-06-01T20:55:42.147460938 1.373496093299845 1.601315240359301 FRB20190601D 1.4985396957623311 1.3849187614575003
b'190601_205515' 2019-06-01T20:55:52.316894531 1.12

b'190612_003512' 2019-06-12T00:35:49.648681641 1.8112253868094106 1.3013307231918332 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003524' 2019-06-12T00:36:01.554687500 1.461302858162008 1.4653037673964209 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003538' 2019-06-12T00:36:15.517578125 1.0067837805917264 1.8402019564250898 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003600' 2019-06-12T00:36:37.802246094 1.2613591991657165 1.2452365424024148 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003620' 2019-06-12T00:36:57.410156250 1.581071659912339 1.972946690771346 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003658' 2019-06-12T00:37:35.579345703 1.2348176321197817 1.1216615954351699 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003722' 2019-06-12T00:37:59.044189453 1.8283133966584135 1.9725420604340145 FRB20190612A 2.5858798197547985 1.229060859254407
b'190612_003747' 2019-06-12T00:38:24.166748047 1.055183397

b'190623_075435' 2019-06-23T07:55:12.434814453 1.3506538750593409 1.6642420290472315 FRB20190623A 4.720766560794263 0.42795473258900957
b'190623_075538' 2019-06-23T07:56:15.383300781 1.5987773143175243 1.9648508271091052 FRB20190623A 4.720766560794263 0.42795473258900957
b'190623_075650' 2019-06-23T07:57:27.273437500 1.0326057285770058 1.176411633390308 FRB20190623A 4.720766560794263 0.42795473258900957
b'190623_075712' 2019-06-23T07:57:49.841064453 1.7874142152103198 1.8112942897584805 FRB20190623A 4.720766560794263 0.42795473258900957
b'190623_121449' 2019-06-23T12:15:26.949218750 1.237808079563905 1.953860089055257 FRB20190623B 5.850692718535392 0.8049458510197847
b'190623_121513' 2019-06-23T12:15:50.445800781 1.4372279148571483 1.4820325180058151 FRB20190623B 5.850692718535392 0.8049458510197847
b'190623_121536' 2019-06-23T12:16:13.886474609 1.3631069918386218 1.0241809571183436 FRB20190623B 5.850692718535392 0.8049458510197847
b'190623_121551' 2019-06-23T12:16:28.722656250 1.74041

b'190701_094922' 2019-07-01T09:49:59.381591797 1.236840861078106 1.6554036286303218 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_094934' 2019-07-01T09:50:11.346923828 1.129872862426737 1.0647976254552705 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_094952' 2019-07-01T09:50:29.173095703 1.5076273767507313 1.220396123118878 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_095008' 2019-07-01T09:50:45.309326172 1.2788284647780315 1.4045439586794677 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_095028' 2019-07-01T09:51:05.633056641 1.0018389874972493 1.0158292007723064 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_095057' 2019-07-01T09:51:34.002197266 1.918254531142935 1.845101702599899 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_095125' 2019-07-01T09:52:02.441894531 1.985115048107289 1.3132572049542506 FRB20190701B 5.287125903066423 1.3994049942490534
b'190701_095149' 2019-07-01T09:52:26.062500000 1.006148459046

In [44]:
name_gw[gw_co_idx]

array([b'190403_023537', b'190403_023559', b'190403_023610', ...,
       b'190701_223225', b'190701_223255', b'190701_223306'], dtype='|S13')

In [56]:
addfrbname = []
for gwname in df['gwname']:
    ii = np.where(name_gw[gw_co_idx]==gwname.encode())[0]
    frbi = left[gw_co_idx[ii]]
    addfrbname.append(name_frb[frbi][0])

In [57]:
df['frbname'] = addfrbname

In [58]:
df

gwname      fix_lnb     relax_lnb    gwstat      ranking  \
0     190701_223118    11.301643      7.331421  4.952719     8.922941   
1     190605_021909    12.771765      9.127000  3.862183     7.506948   
2     190411_050213    10.246110      6.976561  3.681050     6.950599   
3     190520_102326     5.990904      3.872832  4.148149     6.266221   
4     190409_032650    11.120391      7.384171  2.218422     5.954642   
...             ...          ...           ...       ...          ...   
1045  190519_230244   604.206402    761.931638  2.434241  -155.290995   
1046  190612_195828   406.788341    624.079481 -1.029691  -218.320830   
1047  190519_230231   840.912410   1060.075528 -3.614769  -222.777887   
1048  190518_223900   367.513293    589.391614 -2.869363  -224.747685   
1049  190621_081615  8315.252956  12616.639059 -1.468428 -4302.854531   

           frbname  
0     FRB20190701E  
1     FRB20190605C  
2     FRB20190411B  
3     FRB20190520A  
4     FRB20190409B  
...            ...  
1045  FRB20190519J  
1046  FRB20190612C  
1047  FRB20190519J  
1048  FRB20190518G  
1049  FRB20190621D  

[1050 rows x 6 columns]

In [59]:
cols = df.columns.tolist()

In [60]:
cols = cols[-1:] + cols[:-1]

In [61]:
df = df[cols]

In [62]:
df

frbname         gwname      fix_lnb     relax_lnb    gwstat  \
0     FRB20190701E  190701_223118    11.301643      7.331421  4.952719   
1     FRB20190605C  190605_021909    12.771765      9.127000  3.862183   
2     FRB20190411B  190411_050213    10.246110      6.976561  3.681050   
3     FRB20190520A  190520_102326     5.990904      3.872832  4.148149   
4     FRB20190409B  190409_032650    11.120391      7.384171  2.218422   
...            ...            ...          ...           ...       ...   
1045  FRB20190519J  190519_230244   604.206402    761.931638  2.434241   
1046  FRB20190612C  190612_195828   406.788341    624.079481 -1.029691   
1047  FRB20190519J  190519_230231   840.912410   1060.075528 -3.614769   
1048  FRB20190518G  190518_223900   367.513293    589.391614 -2.869363   
1049  FRB20190621D  190621_081615  8315.252956  12616.639059 -1.468428   

          ranking  
0        8.922941  
1        7.506948  
2        6.950599  
3        6.266221  
4        5.954642  
...           ...  
1045  -155.290995  
1046  -218.320830  
1047  -222.777887  
1048  -224.747685  
1049 -4302.854531  

[1050 rows x 6 columns]

In [63]:
df.to_csv('candidate.csv',index=False)

# Postprocessing

In [33]:
df = pd.read_csv('../results.csv')

In [38]:
for i in range(3):
    gwname = df['name'][i]
    print(gwname)
    ind = np.where(name_gw[gw_co_idx]==gwname.encode())[0]
    frbi = left[gw_co_idx[ind]]
    print(name_frb[frbi],Time(t_frb[np.where(name_frb==name_frb[frbi])],format='gps').datetime64,Time(time_gw[gw_co_idx][ind],format='gps').datetime64)

190409_114158
['FRB20190409C'] ['2019-04-09T11:43:59.507593632'] ['2019-04-09T11:42:35.831542969']
190701_223118
['FRB20190701E'] ['2019-07-01T22:32:17.497723579'] ['2019-07-01T22:31:55.256103516']
190409_032650
['FRB20190409B'] ['2019-04-09T03:26:09.640700579'] ['2019-04-09T03:27:27.323730469']


# Make events.ini. 
## First, fix_sky

In [33]:
%mkdir -p /work/yifan.wang/em/t1/triggers
%mkdir -p /work/yifan.wang/em/t1/fix_sky
%mkdir -p /work/yifan.wang/em/t1/relax_sky/

In [34]:
gw_co_idx

array([  3708,   3709,   3710, ..., 294238, 294239, 294240])

In [35]:
len(gw_co_idx)

1050

# Write triggers files

In [36]:
fixskydir = '/work/yifan.wang/em/t1/triggers/'
try:
    shutil.rmtree(fixskydir)
except FileNotFoundError:
    pass

os.mkdir(fixskydir)
itrig = 0

for ii,vv in enumerate(gw_co_idx):
    print('#########################')
    print('Trigger from GRB/GW search: ',name_gw[vv])
    with open(fixskydir + 'trigger_'+str(itrig)+'.ini', 'w') as t:
        #This line can't be cut into multiple lines or if fails with "string format" issues
        t.write('[trigger]\nmass1=%f\nmass2=%f\nspin1z=%f\nspin2z=%f\nra=%f\ndec=%f\ntrigger_time=%f' % 
                (mass1[vv],
                 mass2[vv],
                 spin1z[vv],
                 spin2z[vv],
                 #the iith frb_co_idx
                 #vv = gw_co_idx(ii)
                 ra_frb[frb_co_idx[ii]],dec_frb[frb_co_idx[ii]],
                 time_gw[vv])
               )
        t.close()
        itrig  +=1

#########################
Trigger from GRB/GW search:  b'190403_023537'
#########################
Trigger from GRB/GW search:  b'190403_023559'
#########################
Trigger from GRB/GW search:  b'190403_023610'
#########################
Trigger from GRB/GW search:  b'190403_023639'
#########################
Trigger from GRB/GW search:  b'190403_023702'
#########################
Trigger from GRB/GW search:  b'190403_023746'
#########################
Trigger from GRB/GW search:  b'190403_023816'
#########################
Trigger from GRB/GW search:  b'190403_023841'
#########################
Trigger from GRB/GW search:  b'190403_041823'
#########################
Trigger from GRB/GW search:  b'190403_041850'
#########################
Trigger from GRB/GW search:  b'190403_041914'
#########################
Trigger from GRB/GW search:  b'190403_041927'
#########################
Trigger from GRB/GW search:  b'190403_041947'
#########################
Trigger from GRB/GW search:  b'190403_

#########################
Trigger from GRB/GW search:  b'190421_232615'
#########################
Trigger from GRB/GW search:  b'190421_232634'
#########################
Trigger from GRB/GW search:  b'190421_232707'
#########################
Trigger from GRB/GW search:  b'190421_232735'
#########################
Trigger from GRB/GW search:  b'190421_232748'
#########################
Trigger from GRB/GW search:  b'190421_232803'
#########################
Trigger from GRB/GW search:  b'190421_232836'
#########################
Trigger from GRB/GW search:  b'190421_232858'
#########################
Trigger from GRB/GW search:  b'190421_232911'
#########################
Trigger from GRB/GW search:  b'190422_042845'
#########################
Trigger from GRB/GW search:  b'190422_042857'
#########################
Trigger from GRB/GW search:  b'190422_042909'
#########################
Trigger from GRB/GW search:  b'190422_042938'
#########################
Trigger from GRB/GW search:  b'190422_

#########################
Trigger from GRB/GW search:  b'190519_153331'
#########################
Trigger from GRB/GW search:  b'190519_153348'
#########################
Trigger from GRB/GW search:  b'190519_153413'
#########################
Trigger from GRB/GW search:  b'190519_153435'
#########################
Trigger from GRB/GW search:  b'190519_153450'
#########################
Trigger from GRB/GW search:  b'190519_230231'
#########################
Trigger from GRB/GW search:  b'190519_230244'
#########################
Trigger from GRB/GW search:  b'190519_230301'
#########################
Trigger from GRB/GW search:  b'190519_230322'
#########################
Trigger from GRB/GW search:  b'190519_230337'
#########################
Trigger from GRB/GW search:  b'190519_230349'
#########################
Trigger from GRB/GW search:  b'190519_230407'
#########################
Trigger from GRB/GW search:  b'190519_230438'
#########################
Trigger from GRB/GW search:  b'190519_

#########################
Trigger from GRB/GW search:  b'190612_053036'
#########################
Trigger from GRB/GW search:  b'190612_053112'
#########################
Trigger from GRB/GW search:  b'190612_053146'
#########################
Trigger from GRB/GW search:  b'190612_053157'
#########################
Trigger from GRB/GW search:  b'190612_195659'
#########################
Trigger from GRB/GW search:  b'190612_195712'
#########################
Trigger from GRB/GW search:  b'190612_195736'
#########################
Trigger from GRB/GW search:  b'190612_195803'
#########################
Trigger from GRB/GW search:  b'190612_195828'
#########################
Trigger from GRB/GW search:  b'190612_195839'
#########################
Trigger from GRB/GW search:  b'190612_195901'
#########################
Trigger from GRB/GW search:  b'190612_195923'
#########################
Trigger from GRB/GW search:  b'190612_195934'
#########################
Trigger from GRB/GW search:  b'190612_

#########################
Trigger from GRB/GW search:  b'190628_055712'
#########################
Trigger from GRB/GW search:  b'190628_055735'
#########################
Trigger from GRB/GW search:  b'190628_055747'
#########################
Trigger from GRB/GW search:  b'190628_055758'
#########################
Trigger from GRB/GW search:  b'190628_055815'
#########################
Trigger from GRB/GW search:  b'190628_142020'
#########################
Trigger from GRB/GW search:  b'190628_142100'
#########################
Trigger from GRB/GW search:  b'190628_142220'
#########################
Trigger from GRB/GW search:  b'190628_142319'
#########################
Trigger from GRB/GW search:  b'190629_135204'
#########################
Trigger from GRB/GW search:  b'190629_135217'
#########################
Trigger from GRB/GW search:  b'190629_135229'
#########################
Trigger from GRB/GW search:  b'190629_135255'
#########################
Trigger from GRB/GW search:  b'190629_

# Write events.ini

In [37]:
eventdir = '/work/yifan.wang/em/t1/fix_sky/events.ini'

try:
    os.remove(eventdir)
except FileNotFoundError:
    pass

ievent = 0
with open(eventdir, 'w') as t:
    
    for ii in gw_co_idx:
        print('#########################')
        print('Trigger from GRB/GW search: ',name_gw[ii])
        t.write('[event-'+str(name_gw[ii].decode())+']\n'+
                'label='+str(name_gw[ii].decode())+'-'+str(ievent)+'\n'+
                'config-files=/work/yifan.wang/em/t1/fixsky_inference.ini\n'+
                '\t/work/yifan.wang/em/t1/o3a.ini\n'+
                '\t/work/yifan.wang/em/t1/triggers/trigger_'+str(ievent)+'.ini\n\n')
        ievent = ievent+1
t.close()

#########################
Trigger from GRB/GW search:  b'190403_023537'
#########################
Trigger from GRB/GW search:  b'190403_023559'
#########################
Trigger from GRB/GW search:  b'190403_023610'
#########################
Trigger from GRB/GW search:  b'190403_023639'
#########################
Trigger from GRB/GW search:  b'190403_023702'
#########################
Trigger from GRB/GW search:  b'190403_023746'
#########################
Trigger from GRB/GW search:  b'190403_023816'
#########################
Trigger from GRB/GW search:  b'190403_023841'
#########################
Trigger from GRB/GW search:  b'190403_041823'
#########################
Trigger from GRB/GW search:  b'190403_041850'
#########################
Trigger from GRB/GW search:  b'190403_041914'
#########################
Trigger from GRB/GW search:  b'190403_041927'
#########################
Trigger from GRB/GW search:  b'190403_041947'
#########################
Trigger from GRB/GW search:  b'190403_

#########################
Trigger from GRB/GW search:  b'190426_012745'
#########################
Trigger from GRB/GW search:  b'190426_012802'
#########################
Trigger from GRB/GW search:  b'190426_012813'
#########################
Trigger from GRB/GW search:  b'190426_012834'
#########################
Trigger from GRB/GW search:  b'190426_012846'
#########################
Trigger from GRB/GW search:  b'190426_012908'
#########################
Trigger from GRB/GW search:  b'190426_012926'
#########################
Trigger from GRB/GW search:  b'190427_225245'
#########################
Trigger from GRB/GW search:  b'190427_225300'
#########################
Trigger from GRB/GW search:  b'190427_225336'
#########################
Trigger from GRB/GW search:  b'190427_225428'
#########################
Trigger from GRB/GW search:  b'190427_225445'
#########################
Trigger from GRB/GW search:  b'190427_225520'
#########################
Trigger from GRB/GW search:  b'190427_

#########################
Trigger from GRB/GW search:  b'190518_090358'
#########################
Trigger from GRB/GW search:  b'190518_090409'
#########################
Trigger from GRB/GW search:  b'190518_090421'
#########################
Trigger from GRB/GW search:  b'190518_090434'
#########################
Trigger from GRB/GW search:  b'190518_090507'
#########################
Trigger from GRB/GW search:  b'190518_090539'
#########################
Trigger from GRB/GW search:  b'190518_090550'
#########################
Trigger from GRB/GW search:  b'190518_090608'
#########################
Trigger from GRB/GW search:  b'190518_223900'
#########################
Trigger from GRB/GW search:  b'190518_223911'
#########################
Trigger from GRB/GW search:  b'190518_223928'
#########################
Trigger from GRB/GW search:  b'190518_223939'
#########################
Trigger from GRB/GW search:  b'190518_223956'
#########################
Trigger from GRB/GW search:  b'190518_

#########################
Trigger from GRB/GW search:  b'190701_205246'
#########################
Trigger from GRB/GW search:  b'190701_205322'
#########################
Trigger from GRB/GW search:  b'190701_205338'
#########################
Trigger from GRB/GW search:  b'190701_205351'
#########################
Trigger from GRB/GW search:  b'190701_205402'
#########################
Trigger from GRB/GW search:  b'190701_205419'
#########################
Trigger from GRB/GW search:  b'190701_205442'
#########################
Trigger from GRB/GW search:  b'190701_205456'
#########################
Trigger from GRB/GW search:  b'190701_205511'
#########################
Trigger from GRB/GW search:  b'190701_223007'
#########################
Trigger from GRB/GW search:  b'190701_223021'
#########################
Trigger from GRB/GW search:  b'190701_223033'
#########################
Trigger from GRB/GW search:  b'190701_223045'
#########################
Trigger from GRB/GW search:  b'190701_

# Then relax the sky position

In [38]:
eventdir = '/work/yifan.wang/em/t1/relax_sky/events.ini'

try:
    os.remove(eventdir)
except FileNotFoundError:
    pass

ievent = 0
with open(eventdir, 'w') as t:
    
    for ii in gw_co_idx:
        print('#########################')
        print('Trigger from GRB/GW search: ',name_gw[ii])
        t.write('[event-'+str(name_gw[ii].decode())+']\n'+
                'label='+str(name_gw[ii].decode())+'-'+str(ievent)+'\n'+
                'config-files=/work/yifan.wang/em/t1/relaxsky_inference.ini\n'+
                '\t/work/yifan.wang/em/t1/o3a.ini\n'+
                '\t/work/yifan.wang/em/t1/triggers/trigger_'+str(ievent)+'.ini\n\n')
        ievent = ievent+1
t.close()

#########################
Trigger from GRB/GW search:  b'190403_023537'
#########################
Trigger from GRB/GW search:  b'190403_023559'
#########################
Trigger from GRB/GW search:  b'190403_023610'
#########################
Trigger from GRB/GW search:  b'190403_023639'
#########################
Trigger from GRB/GW search:  b'190403_023702'
#########################
Trigger from GRB/GW search:  b'190403_023746'
#########################
Trigger from GRB/GW search:  b'190403_023816'
#########################
Trigger from GRB/GW search:  b'190403_023841'
#########################
Trigger from GRB/GW search:  b'190403_041823'
#########################
Trigger from GRB/GW search:  b'190403_041850'
#########################
Trigger from GRB/GW search:  b'190403_041914'
#########################
Trigger from GRB/GW search:  b'190403_041927'
#########################
Trigger from GRB/GW search:  b'190403_041947'
#########################
Trigger from GRB/GW search:  b'190403_

Trigger from GRB/GW search:  b'190612_195828'
#########################
Trigger from GRB/GW search:  b'190612_195839'
#########################
Trigger from GRB/GW search:  b'190612_195901'
#########################
Trigger from GRB/GW search:  b'190612_195923'
#########################
Trigger from GRB/GW search:  b'190612_195934'
#########################
Trigger from GRB/GW search:  b'190612_195948'
#########################
Trigger from GRB/GW search:  b'190612_200008'
#########################
Trigger from GRB/GW search:  b'190613_074339'
#########################
Trigger from GRB/GW search:  b'190613_074402'
#########################
Trigger from GRB/GW search:  b'190613_074416'
#########################
Trigger from GRB/GW search:  b'190613_074447'
#########################
Trigger from GRB/GW search:  b'190613_074511'
#########################
Trigger from GRB/GW search:  b'190613_074628'
#########################
Trigger from GRB/GW search:  b'190613_185526'
##################

Trigger from GRB/GW search:  b'190621_081615'
#########################
Trigger from GRB/GW search:  b'190622_094432'
#########################
Trigger from GRB/GW search:  b'190622_094448'
#########################
Trigger from GRB/GW search:  b'190622_094506'
#########################
Trigger from GRB/GW search:  b'190622_094548'
#########################
Trigger from GRB/GW search:  b'190622_094558'
#########################
Trigger from GRB/GW search:  b'190622_094614'
#########################
Trigger from GRB/GW search:  b'190622_094628'
#########################
Trigger from GRB/GW search:  b'190622_094649'
#########################
Trigger from GRB/GW search:  b'190622_094705'
#########################
Trigger from GRB/GW search:  b'190623_075435'
#########################
Trigger from GRB/GW search:  b'190623_075538'
#########################
Trigger from GRB/GW search:  b'190623_075650'
#########################
Trigger from GRB/GW search:  b'190623_075712'
##################

# Make background: Time window [-100,100]

In [39]:
n = 100
step = (tO3_end.gps - tO3_start.gps) / (n+1)

trigdir = '/work/yifan.wang/em/t2-background/trigger/'
try:
    shutil.rmtree(trigdir)
except FileNotFoundError:
    pass

os.mkdir(trigdir)


for nvalue in range(n):
    print('chunk:',nvalue)
    
    offset = (nvalue + 1) * step
    t_frb_timeslide = (t_frb + offset) % tO3_end.gps + (t_frb+offset)//tO3_end.gps * tO3_start.gps
    
    # sort the t_frb
    sortfrb = np.argsort(t_frb_timeslide)
    t_frb_timeslide = t_frb_timeslide[sortfrb]
    ra_timeslide = ra_frb[sortfrb]
    dec_timeslide = dec_frb[sortfrb]
    #[t_frb ---100s--- t_gw ----------- 100s ------------- t_frb]
    left = np.searchsorted(t_frb_timeslide, time_gw - 100)
    right = np.searchsorted(t_frb_timeslide, time_gw + 100)

    gw_co_idx = np.where((right - left) > 0)[0]
    frb_co_idx = left[gw_co_idx]
    print('There are ', len(gw_co_idx), 'coincidence.')

    itrig = 0

    for ii,vv in enumerate(gw_co_idx):
        with open(trigdir + 'trigger_chunk'+str(nvalue)+'_'+str(itrig)+'.ini', 'w') as t:
        #This line can't be cut into multiple lines or if fails with "string format" issues
            t.write('[trigger]\nmass1=%f\nmass2=%f\nspin1z=%f\nspin2z=%f\nra=%f\ndec=%f\ntrigger_time=%f' % 
                (mass1[vv],
                 mass2[vv],
                 spin1z[vv],
                 spin2z[vv],
                 #the iith frb_co_idx
                 #vv = gw_co_idx(ii)
                 ra_timeslide[frb_co_idx[ii]],dec_timeslide[frb_co_idx[ii]],
                 time_gw[vv])
                  )
            t.close()
            itrig  +=1

chunk: 0
There are  1086 coincidence.
chunk: 1
There are  1125 coincidence.
chunk: 2
There are  1085 coincidence.
chunk: 3
There are  1165 coincidence.
chunk: 4
There are  1223 coincidence.
chunk: 5
There are  1032 coincidence.
chunk: 6
There are  1086 coincidence.
chunk: 7
There are  1183 coincidence.
chunk: 8
There are  1102 coincidence.
chunk: 9
There are  1097 coincidence.
chunk: 10
There are  1157 coincidence.
chunk: 11
There are  1059 coincidence.
chunk: 12
There are  1174 coincidence.
chunk: 13
There are  1007 coincidence.
chunk: 14
There are  1107 coincidence.
chunk: 15
There are  971 coincidence.
chunk: 16
There are  1025 coincidence.
chunk: 17
There are  1166 coincidence.
chunk: 18
There are  1146 coincidence.
chunk: 19
There are  1131 coincidence.
chunk: 20
There are  1033 coincidence.
chunk: 21
There are  1109 coincidence.
chunk: 22
There are  1141 coincidence.
chunk: 23
There are  1183 coincidence.
chunk: 24
There are  1128 coincidence.
chunk: 25
There are  1123 coincidenc

In [40]:
sortfrb

array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
        14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,
        40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
        53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  65,
        66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,  78,
        79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,  91,
        92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103, 104,
       105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117,
       118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130,
       131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143,
       144, 145, 146, 147, 148, 149, 150,   0])

In [42]:
ra_timeslide

array([3.11733258, 1.42663213, 2.03034152, 2.36439754, 4.36035607,
       5.69902361, 3.84356408, 0.7564257 , 2.49756616, 4.53419086,
       5.88210865, 4.12735462, 4.5762533 , 1.38788582, 2.2104595 ,
       4.40870169, 5.87547639, 4.59841898, 4.63838702, 1.3962634 ,
       2.68833065, 0.16283922, 4.24900406, 4.98553301, 3.16672539,
       4.30921792, 3.18313149, 0.15463617, 1.30568081, 2.53055288,
       3.00528244, 3.05205726, 0.7972664 , 1.14825211, 1.83224665,
       4.45530198, 1.6533504 , 1.85964832, 4.33016187, 1.4397221 ,
       2.76233261, 0.84753188, 3.1360076 , 5.21120408, 6.09259535,
       0.51818825, 2.93738913, 4.46315596, 3.66728582, 2.00782677,
       1.37758838, 2.97980063, 4.90594599, 5.7583648 , 4.1489967 ,
       1.35612083, 4.83840175, 4.56316333, 2.8799678 , 3.70079615,
       2.71573232, 5.41313868, 0.01448623, 1.17163953, 2.92063397,
       5.93324679, 1.5271631 , 3.05624605, 4.22387132, 3.04943927,
       1.6543976 , 2.87228835, 2.93704007, 2.89078884, 5.35257

# Verification

In [ ]:
pylab.hist(t_frb_timeslide[frb_co_idx] - time_gw[gw_co_idx])